In [4]:
import pandas as pd
from bs4 import BeautifulSoup

df = pd.read_csv('./bq-results-20211206-133858-irtkgx60el7i.csv').drop(['ParentUrl', 'ParentAuthor', 'ParentTime', 'ParentScore'], axis=1)
df.text = df.text.str.replace('<p>', '\n')
strings_to_remove = ['rel="nofollow"', '<pre>', '</pre>', '<i>', '</i>', '<code>', '</code>', '&gt;']
email_regex = '[a-zA-Z0-9._-]{0,30}@[a-zA-Z0-9._-]{0,20}\.[a-zA-Z0-9_-]{2,3}'
munged_url_regex = 'http(s)?:\&\#.*?\<\/a>'

for string in strings_to_remove:
    df.text = df.text.str.replace(string, '')


df.text = df.text.replace(email_regex, 'REDACTED_EMAIL', regex=True)
df.text = df.text.replace(munged_url_regex, '', regex=True)

    # fix some unicode issues
df.text = df.text.str.replace('&#x27;', "'")
df.text = df.text.str.replace('&#x2F;', "/")
df.text = df.text.str.replace("&quot;", '"')

hiring_df = df[df.ParentTitle.str.lower().str.contains('who is hiring')]
wants_to_be_hired_df = df[df.ParentTitle.str.lower().str.contains('wants to be hired')]
freelancer_df = df[df.ParentTitle.str.lower().str.contains('freelancer')]


/usr/local/anaconda3/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3165: DtypeWarning: Columns (4) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


In [24]:
import datasets
from huggingface_hub import create_repo
from huggingface_hub import Repository

In [43]:
all_datasets = datasets.dataset_dict.DatasetDict({'hiring': datasets.Dataset.from_pandas(hiring_df),
                                                  'wants_to_be_hired': datasets.Dataset.from_pandas(wants_to_be_hired_df),
                                                  'freelancer': datasets.Dataset.from_pandas(freelancer_df)})
data_path = './data'
all_datasets.save_to_disk(data_path)

repo_url = 'https://huggingface.co/datasets/dansbecker/hackernews_hiring_posts'
repo = Repository(local_dir=".", clone_from=repo_url)
repo.git_pull()
repo.git_add(data_path)
repo.git_commit("Push data from notebook")

/Users/dan.becker/Desktop/hackernews_hiring_dataset is already a clone of https://huggingface.co/datasets/dansbecker/hackernews_hiring_posts. Make sure you pull the latest changes with `repo.git_pull()`.


OSError: fatal: pathspec 'hackernews_hiring_dataset/data/*' did not match any files


In [36]:
repo.git_commit?

Signature: repo.git_commit(commit_message: str = 'commit files to HF hub')
Docstring: git commit
File:      /usr/local/anaconda3/lib/python3.8/site-packages/huggingface_hub/repository.py
Type:      method


TypeError: Expected a pyarrow.Table or a datasets.table.Table object, but got {'hiring':                                                      text  \
0       Kindling -- New York City\nLead Application De...   
1       Angular UI Developers: Help Improve the State ...   
2       Cir.cl is a funded startup founded by former O...   
3       Backplane - Palo Alto, CA\n== About Us ==\nWe ...   
5       We are building supercomputers and bespoke sof...   
...                                                   ...   
111574  LOCATION: Mountain View, CA |Full-time |ONSITE...   
111575  Eaze | Senior Software Engineer | San Francisc...   
111576  Auckland, New Zealand | REMOTE | VISA\n---\n# ...   
111577  Elementum | Mountain View | Onsite\nI am the H...   
111578  SeatGeek — New York, NY — Full Time — We're a ...   

                    CommentTime  CommentAuthor  \
0       2014-08-01 16:15:39 UTC       toestues   
1       2014-08-01 16:15:52 UTC    AngularJobs   
2       2014-05-01 20:50:30 